In [1]:

import torch
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "2"

import sys
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))

#use gpu number 3 
device=torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

#file_id=6448
file_id=23114

base_path="/home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/"
file_dry=os.path.join(base_path, "dry",str(file_id),"vocals.wav")
file_wet=os.path.join(base_path, "wet",str(file_id),"vocals.wav")

import soundfile as sf

print("Loading files:", file_dry, file_wet)
dry, sr = sf.read(file_dry)
print("Loading files:", file_dry, file_wet)
wet, sr = sf.read(file_wet)
print("files loaded")

#file_dry_fxnorm, sr=sf.read(file_dry_fxnorm_dr)
#file_wet_fxnorm, sr=sf.read(file_wet_fxnorm_dr)

dry=torch.from_numpy(dry.T).float().unsqueeze(0)
wet=torch.from_numpy(wet.T).float().unsqueeze(0)

#dry_fxnorm=torch.from_numpy(file_dry_fxnorm.T).float().unsqueeze(0)

dry=dry.mean(dim=1, keepdim=True)

#dry_fxnorm=torch.from_numpy(file_dry_fxnorm.T).float().unsqueeze(0)


start_t=15*sr
segment_length = 524288
wet_segment = wet[...,start_t:start_t + segment_length]


import pyloudnorm as pyln
meter = pyln.Meter(sr)
normaliser = lambda x: pyln.normalize.loudness(
    x, meter.integrated_loudness(x), -18.0
)

print("dry", dry.shape, dry.min(), dry.max())

dry = torch.from_numpy(normaliser(dry.numpy().T).T).float().to(device)
#wet = torch.from_numpy(normaliser(wet.numpy().T).T).float().to(device)
#dry_fxnorm = torch.from_numpy(normaliser(dry_fxnorm.numpy().T).T).float().to(device)


print("dry", dry.shape,dry.min(), dry.max())
dry_segment = dry[...,start_t:start_t + segment_length]


from IPython.display import Audio

#Audio(dry_segment[0].cpu().numpy(), rate=sr, normalize=False)
Audio(wet_segment[0].cpu().numpy(), rate=sr, normalize=True)

Using device: cuda
Loading files: /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/dry/23114/vocals.wav /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/wet/23114/vocals.wav
Loading files: /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/dry/23114/vocals.wav /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/wet/23114/vocals.wav
files loaded
dry torch.Size([1, 1, 7014686]) tensor(-0.7464) tensor(0.7499)
dry torch.Size([1, 1, 7014686]) tensor(-0.8735, device='cuda:0') tensor(0.8776, device='cuda:0')


In [19]:
wet_segment.shape

torch.Size([1, 2, 524288])

In [16]:
from utils.common_audioeffects import AugmentationChain, ConvolutionalReverb, Compressor, Equaliser, Panner, Haas
from glob import glob

RIR_path_csv="/data5/eloi/ImpulseResponses/rir_files_train.csv"

import pandas as pd
df= pd.read_csv(RIR_path_csv)
#list of RIR files
RIR_files = df['rir_file'].tolist()
print(RIR_files[:10])

acceoted_sampling_rates = [44100]



import pandas as pd
import soundfile as sf
dataset_rir=pd.DataFrame(columns=['impulse_response'])
for i, file in enumerate(RIR_files):
    #load the RIR file
    x,fs=sf.read(file)
    n_samples=x.shape[0]
    if len(x.shape) == 1:
        x = x[:, None]
    my_tuple=(int(n_samples), x)
    #add my_tuple to the dataset_rir DataFrame (column 'impulse_response')
    dataset_rir.loc[i, 'impulse_response'] = my_tuple


augment_chain= AugmentationChain([
                    (ConvolutionalReverb(impulse_responses=dataset_rir, sample_rates=acceoted_sampling_rates), 0.5),
                    (Haas(sample_rates=acceoted_sampling_rates), 0.5),
                    (Panner(sample_rates=acceoted_sampling_rates), 0.5),
                    (Compressor(sample_rates=acceoted_sampling_rates), 0.5),
                    (Equaliser(n_channels=2,sample_rates=acceoted_sampling_rates), 0.5),
                    ],
                    shuffle=True, apply_to='target')




augmented_input, augmented_target = augment_chain(dry_segment[0].cpu().numpy().T, wet_segment[0].cpu().numpy().T)




['/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-449/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-4416/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-3928/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-4395/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-4290/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-4421/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-4185/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-4251/impulse_response.wav', '/data5/eloi/ImpulseResponses/FabFilterProR/RT60_avg/5500-6000/impulse_response-4414/impulse_response.wav', '/data5/eloi/ImpulseResponse

In [17]:
Audio(augmented_target.T, rate=sr, normalize=True)